# 1 - IMPORTS

In [49]:
import pandas as pd
import plotly.express as px
from haversine import haversine
import folium

# 2 - Data

In [50]:
data = pd.read_csv('data/uber.csv')
df = data.copy()
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200000 entries, 0 to 199999
Data columns (total 9 columns):
 #   Column             Non-Null Count   Dtype  
---  ------             --------------   -----  
 0   Unnamed: 0         200000 non-null  int64  
 1   key                200000 non-null  object 
 2   fare_amount        200000 non-null  float64
 3   pickup_datetime    200000 non-null  object 
 4   pickup_longitude   200000 non-null  float64
 5   pickup_latitude    200000 non-null  float64
 6   dropoff_longitude  199999 non-null  float64
 7   dropoff_latitude   199999 non-null  float64
 8   passenger_count    200000 non-null  int64  
dtypes: float64(5), int64(2), object(2)
memory usage: 13.7+ MB


In [51]:
data.head()

Unnamed: 0                            key  fare_amount  \
0    24238194    2015-05-07 19:52:06.0000003          7.5   
1    27835199    2009-07-17 20:04:56.0000002          7.7   
2    44984355   2009-08-24 21:45:00.00000061         12.9   
3    25894730    2009-06-26 08:22:21.0000001          5.3   
4    17610152  2014-08-28 17:47:00.000000188         16.0   

           pickup_datetime  pickup_longitude  pickup_latitude  \
0  2015-05-07 19:52:06 UTC        -73.999817        40.738354   
1  2009-07-17 20:04:56 UTC        -73.994355        40.728225   
2  2009-08-24 21:45:00 UTC        -74.005043        40.740770   
3  2009-06-26 08:22:21 UTC        -73.976124        40.790844   
4  2014-08-28 17:47:00 UTC        -73.925023        40.744085   

   dropoff_longitude  dropoff_latitude  passenger_count  
0         -73.999512         40.723217                1  
1         -73.994710         40.750325                1  
2         -73.962565         40.772647                1  
3         -73.965316         40.803349                3  
4         -73.973082         40.761247                5

In [52]:
# Corrida não finalizada, sem passageiros
data[data['dropoff_latitude'].isna()]

Unnamed: 0                          key  fare_amount  \
87946    32736015  2013-07-02 03:51:57.0000001         24.1   

               pickup_datetime  pickup_longitude  pickup_latitude  \
87946  2013-07-02 03:51:57 UTC        -73.950581        40.779692   

       dropoff_longitude  dropoff_latitude  passenger_count  
87946                NaN               NaN                0

In [53]:
# A coluna 'key' pode ser desconsiderada, contém os mesmos dados de 'pickup_datetime', e já temos uma coluna com o id das corridas
data['Unnamed: 0'].nunique(), data['key'].nunique()

(200000, 200000)

# 3 - Data Transform

In [54]:
# Drop da coluna 'key'
df.drop(columns='key', axis=1, inplace=True)
# Drop da corrida não finalizada
df.dropna(inplace=True)

# Conversão da coluna da data para o formato datetime e criação das colunas de ano, mês e dia,
df['pickup_datetime'] = pd.to_datetime(df['pickup_datetime'])
df['year'] = df['pickup_datetime'].apply(lambda x: x.year)
df['month'] = df['pickup_datetime'].apply(lambda x: x.month)
df['day'] = df['pickup_datetime'].apply(lambda x: x.day)

# Renomeando as colunas 'Unnamed: 0 ' e 'fare_amount'
new_cols = ['id',
 'fare',
 'pickup_date',
 'pickup_longitude',
 'pickup_latitude',
 'dropoff_longitude',
 'dropoff_latitude',
 'passenger_count',
 'year',
 'month',
 'day']

df.columns = new_cols

# Eliminando taxas menores que zero
df = df[df['fare'] > 0]

# Convertendo a data para TimeStamp
df['pickup_timestamp'] = df['pickup_date'].dt.strftime('%Y-%m-%d')


In [55]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 199977 entries, 0 to 199999
Data columns (total 12 columns):
 #   Column             Non-Null Count   Dtype              
---  ------             --------------   -----              
 0   id                 199977 non-null  int64              
 1   fare               199977 non-null  float64            
 2   pickup_date        199977 non-null  datetime64[ns, UTC]
 3   pickup_longitude   199977 non-null  float64            
 4   pickup_latitude    199977 non-null  float64            
 5   dropoff_longitude  199977 non-null  float64            
 6   dropoff_latitude   199977 non-null  float64            
 7   passenger_count    199977 non-null  int64              
 8   year               199977 non-null  int64              
 9   month              199977 non-null  int64              
 10  day                199977 non-null  int64              
 11  pickup_timestamp   199977 non-null  object             
dtypes: datetime64[ns, UTC](1), float64(

# 4 - Explore

## 4.1 - Passengers

In [56]:
df['passenger_count'].value_counts()

passenger_count
1      138414
2       29424
5       14005
3        8878
4        4276
6        4271
0         708
208         1
Name: count, dtype: int64

708 corridas não tiveram passageiros, 1 corrida teve 208 passageiros

In [57]:
# Corrida com 208 passageiros
df[df['passenger_count'] == 208]

id  fare               pickup_date  pickup_longitude  \
113038  35893772  11.7 2010-12-28 08:20:00+00:00        -73.937795   

        pickup_latitude  dropoff_longitude  dropoff_latitude  passenger_count  \
113038        40.758498         -73.937835         40.758415              208   

        year  month  day pickup_timestamp  
113038  2010     12   28       2010-12-28

In [58]:
# Stats geral das corridas com zero passageiros
zero_passengers = df[df['passenger_count'] == 0]
zero_passengers.describe()

id        fare  pickup_longitude  pickup_latitude  \
count  7.080000e+02  708.000000        708.000000       708.000000   
mean   2.675977e+07    9.439266        -71.887276        39.600657   
std    1.596255e+07    6.731690         12.265380         6.756683   
min    1.371400e+04    2.500000        -74.017300         0.000000   
25%    1.325389e+07    5.300000        -73.992202        40.734526   
50%    2.599671e+07    7.300000        -73.980950        40.754720   
75%    4.053639e+07   11.300000        -73.965799        40.767425   
max    5.531657e+07   57.300000          0.000000        40.833400   

       dropoff_longitude  dropoff_latitude  passenger_count         year  \
count         708.000000        708.000000            708.0   708.000000   
mean          -71.989742         39.658641              0.0  2011.355932   
std            11.963165          6.590469              0.0     0.642996   
min           -74.016154          0.000000              0.0  2009.000000   
25%           -73.991022         40.733205              0.0  2011.000000   
50%           -73.979650         40.753200              0.0  2011.000000   
75%           -73.962868         40.769800              0.0  2012.000000   
max             0.000000         40.864822              0.0  2015.000000   

            month         day  
count  708.000000  708.000000  
mean     5.899718   15.524011  
std      3.554363    8.867610  
min      1.000000    1.000000  
25%      3.000000    8.000000  
50%      5.000000   15.000000  
75%      9.000000   23.000000  
max     12.000000   31.000000

## 4.2 - Coordinates

In [59]:
# Localizando colunas com coordenadas (latitude, longitude) iguais à zero
zero_coordenates = df.apply(lambda x: True if any([x['pickup_latitude'] == 0, x['pickup_longitude'] == 0, x['dropoff_latitude'] == 0, x['dropoff_longitude'] == 0]) else False, axis=1)
print(f'Existem {sum(zero_coordenates)} corridas com coordenadas zeradas')

# Eliminando as colunas com coordenadas (latitude, longitude) iguais à zero
df1 = df.copy().reset_index() # criando um novo dataframe para permanecer o estado anterior a estas alterações
df1 = df[~zero_coordenates]

Existem 3965 corridas com coordenadas zeradas


De acordo com uma fonte confiável da Wikipédia (módulo de mapa, que define os limites para fins cartográficos):

Limintes da cidade de NEW YORK

Latitude máxima (topo): aproximadamente 40.92° N

Latitude mínima (base): aproximadamente 40.49° N

Longitude mínima (lado esquerdo): aproximadamente –74.27° (mais a oeste)

Longitude máxima (lado direito): aproximadamente –73.68° (mais a leste) 

In [60]:
# Aplicando os filtros de limites das coordenadas 
mask = (
    (df1['pickup_longitude']  >= -74.27) & (df1['pickup_longitude']  <= -73.68) &
    (df1['dropoff_longitude'] >= -74.27) & (df1['dropoff_longitude'] <= -73.68) &
    (df1['pickup_latitude']   >=  40.49) & (df1['pickup_latitude']   <=  40.92) &
    (df1['dropoff_latitude']  >=  40.49) & (df1['dropoff_latitude']  <=  40.92)
)
df1 = df1[mask]


In [61]:
# Distancia das corridas
coord_cols = ['pickup_longitude',
 'pickup_latitude',
 'dropoff_longitude',
 'dropoff_latitude']

df1['distance'] = df1.loc[:,coord_cols].apply(lambda x: haversine( (x['pickup_latitude'], x['pickup_longitude']), 
                                                                         (x['dropoff_latitude'], x['dropoff_longitude']) ),axis=1)

# Eliminando distancias iguais a zero
df1 = df1[df1['distance'] > 0.5]

In [62]:
px.scatter(df1,x='pickup_longitude',y='pickup_latitude',)

In [63]:
px.scatter(df1, x='distance', y='fare')

In [64]:
# Plotando amostras das posições geográficas de partida e destino das corridas
df_test = df1.sample(1500)

def get_coordinates(df):
    coord_list = []
    for i in zip(df['pickup_latitude'], df['pickup_longitude']):
        coord_list.append(i)
    for i in zip(df['dropoff_latitude'], df['dropoff_longitude']):
        coord_list.append(i)
    
    return coord_list

coordenadas = get_coordinates(df_test)
mapa = folium.Map(location=[df1['pickup_latitude'].mean(), df1['pickup_longitude'].mean()], zoom_start=5)
for i in coordenadas:
    folium.Marker(location=i).add_to(mapa)
# mapa

In [65]:
# Corrida mais distante
df1[df1['distance'] == df1['distance'].max()]

id   fare               pickup_date  pickup_longitude  \
195343  24456114  81.81 2010-10-06 22:15:00+00:00        -73.970932   

        pickup_latitude  dropoff_longitude  dropoff_latitude  passenger_count  \
195343        40.757446           -74.2368         40.511859                1   

        year  month  day pickup_timestamp   distance  
195343  2010     10    6       2010-10-06  35.341909

In [66]:

# Posição de partida e destino da corrida mais distante
mapa = folium.Map(location=[df1['pickup_latitude'].mean(), df1['pickup_longitude'].mean()], zoom_start=10)
folium.Marker(location=[40.511859, -74.2368], popup='dropoff').add_to(mapa)
folium.Marker(location=[40.757446, -73.970932], popup='pickup').add_to(mapa)

#mapa

# 5 - OPEN METEO API

In [67]:
latitude,longitude,date = df1[['pickup_latitude','pickup_longitude','pickup_timestamp']].iloc[0,:]
latitude,longitude,date
date

'2015-05-07'

In [68]:
from open_meteo_api import Weather

latitude,longitude,date = df1[['pickup_latitude','pickup_longitude','pickup_timestamp']].iloc[0,:]
latitude,longitude,date

day_test = Weather(latitude,longitude)

day_test.forecast(date,date)


data         clima
0 2015-05-07 04:00:00+00:00  Mainly Sunny

In [69]:
df1.sample()

id  fare               pickup_date  pickup_longitude  \
29688  48598433   4.9 2010-04-17 12:48:00+00:00        -73.979685   

       pickup_latitude  dropoff_longitude  dropoff_latitude  passenger_count  \
29688        40.735482         -73.987945         40.728133                1   

       year  month  day pickup_timestamp  distance  
29688  2010      4   17       2010-04-17  1.073395

In [70]:
df1.columns.tolist()

['id',
 'fare',
 'pickup_date',
 'pickup_longitude',
 'pickup_latitude',
 'dropoff_longitude',
 'dropoff_latitude',
 'passenger_count',
 'year',
 'month',
 'day',
 'pickup_timestamp',
 'distance']

In [71]:
df1['pickup_day'] = df1['pickup_date'].dt.date.astype(str)

In [72]:
day_test = Weather(40.74148,-73.989674)

d = day_test.forecast('2012-05-23','2012-05-23')
d['clima'].loc[0]

'Rain'

In [73]:
df1[['pickup_latitude','pickup_longitude','pickup_timestamp']]

pickup_latitude  pickup_longitude pickup_timestamp
0             40.738354        -73.999817       2015-05-07
1             40.728225        -73.994355       2009-07-17
2             40.740770        -74.005043       2009-08-24
3             40.790844        -73.976124       2009-06-26
4             40.744085        -73.925023       2014-08-28
...                 ...               ...              ...
199994        40.760770        -73.983070       2014-01-31
199996        40.736837        -73.984722       2014-03-14
199997        40.756487        -73.986017       2009-06-29
199998        40.725452        -73.997124       2015-05-20
199999        40.720077        -73.984395       2010-05-15

[187605 rows x 3 columns]

In [74]:
df1['pickup_day']

0         2015-05-07
1         2009-07-17
2         2009-08-24
3         2009-06-26
4         2014-08-28
             ...    
199994    2014-01-31
199996    2014-03-14
199997    2009-06-29
199998    2015-05-20
199999    2010-05-15
Name: pickup_day, Length: 187605, dtype: object

In [75]:
def get_weather(coordenadas, data):
    try:
        meteo = Weather(coordenadas)
        d = meteo.forecast(data,data)
        return d['clima'].loc[0]
    except:
        return None

In [76]:
sample_50 = df1.sample(50)

In [78]:
df1['weather']=sample_50.apply(lambda x: get_weather((x['pickup_longitude'],x['pickup_latitude']),x['pickup_day']),axis=1)

In [80]:
df1['weather'].value_counts()

Series([], Name: count, dtype: int64)